In [18]:
import pandas as pd
import mysql.connector
import uuid

In [28]:
#db details
db = mysql.connector.connect(
    host='localhost',
    user='root',
    password='password',
    database='source_open',
    auth_plugin='mysql_native_password'
)

In [6]:
cursor = db.cursor()

In [6]:
## creating relations

# creating relation Article
query = """CREATE TABLE Article (
    ArticleID VARCHAR(255),
    URL VARCHAR(255),
    PRIMARY KEY (ArticleID));"""
cursor.execute(query)
db.commit()

# creating relation ArticleDetails
query = """CREATE TABLE ArticleDetails (
    URL VARCHAR(255), 
    Headline VARCHAR(255),
    PubName VARCHAR(255),
    PRIMARY KEY (URL));"""
cursor.execute(query)
db.commit()

# creating relation Author
query = """CREATE TABLE Author (
    AuthorID VARCHAR(255),
    AuthorName VARCHAR(255),
    PRIMARY KEY (AuthorID));"""
cursor.execute(query)
db.commit()

# creating relation claim
query = """CREATE TABLE Claim (
    ClaimID VARCHAR(255),
    Type VARCHAR(255),
    NumCitations INT,
    text VARCHAR(10000),
    PRIMARY KEY (ClaimID));"""
cursor.execute(query)
db.commit()

# creating relation CollectionOf
query = """CREATE TABLE CollectionOf (
    ArticleID VARCHAR(255),
    ClaimID VARCHAR(255),
    PRIMARY KEY (ArticleID, ClaimID));"""
cursor.execute(query)
db.commit()

# creating relation WrittenBy
query = """CREATE TABLE WrittenBy (
    AuthorID VARCHAR(255),
    ArticleID VARCHAR(255),
    Date DATE,
    PRIMARY KEY (AuthorID, ArticleID));"""
cursor.execute(query)
db.commit()

# creating relation Publisher
query = """CREATE TABLE Publisher (
    PubName VARCHAR(255),
    PRIMARY KEY (PubName));"""
cursor.execute(query)
db.commit()

NameError: name 'cursor' is not defined

In [26]:
# creating procedures

query = """

CREATE PROCEDURE FindClaimsByTyp(IN claimType VARCHAR(255))
BEGIN
    SELECT claimText FROM Claim WHERE claimType = claimType;
    END
    """
cursor.execute(query)
db.commit()

query = """
CREATE PROCEDURE FindClaimsByTypeAndCitation(IN claimType VARCHAR(255), IN minAuthenticity INT)
BEGIN
    SELECT C.ClaimID, AD.Headline
    FROM Claim C, ArticleDetails AD, Article A, CollectionOf CO
    WHERE C.Type = claimType
	AND AD.URL = A.URL
	AND A.ArticleID = CO.ArticleID
	AND C.ClaimID = CO.ClaimID
    AND C.NumCitations >= minAuthenticity;"""
cursor.execute(query)
db.commit()

query = """CREATE PROCEDURE FindArticlesByKeywor(IN searchKeyword VARCHAR(255))
      BEGIN
              SELECT *
              FROM ArticleDetails
              WHERE Headline LIKE CONCAT('%', searchKeyword, '%');
      END;"""
      
cursor.execute(query)
db.commit()

Done


ProgrammingError: 1064 (42000): You have an error in your SQL syntax; check the manual that corresponds to your MySQL server version for the right syntax to use near '' at line 9

In [7]:
def add_article_details(connection, url, headline, pub_name):
    try:
        cursor = connection.cursor()

        query = "INSERT INTO ArticleDetails (URL, Headline, PubName) VALUES (%s, %s, %s)"
        values = (url, headline, pub_name)

        cursor.execute(query, values)
        connection.commit()

        print("ArticleDetails added successfully!")

    except mysql.connector.Error as err:
        print("Error:", err)

In [8]:
def add_article(connection, article_id, article_url):
    try:
        cursor = connection.cursor()

        # SQL query
        query = "INSERT INTO Article (ArticleID, URL) VALUES (%s, %s)"
        values = (article_id, article_url)

        cursor.execute(query, values)
        connection.commit()

        print("Article added successfully!")

    except mysql.connector.Error as err:
        print("Error:", err)

In [9]:
def add_publisher(connection, pub_name):
    try:
        cursor = connection.cursor()

        query = "INSERT INTO Publisher (PubName) VALUES (%s)"
        values = (pub_name,)

        cursor.execute(query, values)
        connection.commit()

        print("Publisher added successfully!")

    except mysql.connector.Error as err:
        print("Error:", err)

In [10]:
def add_author(connection, author_id, author_name):
    try:
        cursor = connection.cursor()

        query = "INSERT INTO Author (AuthorID, AuthorName) VALUES (%s, %s)"
        values = (author_id, author_name)

        cursor.execute(query, values)
        connection.commit()

        print("Author added successfully!")

    except mysql.connector.Error as err:
        print("Error:", err)

In [11]:
def add_claim(connection, claim_id, claim_type, num_citations, text):
    try:
        cursor = connection.cursor()

        query = "INSERT INTO Claim (ClaimID, Type, NumCitations, text) VALUES (%s, %s, %s,%s)"
        values = (claim_id, claim_type, num_citations, text)

        cursor.execute(query, values)
        connection.commit()

        print("Claim added successfully!")
    except mysql.connector.Error as err:
        print("Error:", err)

In [12]:
def add_collectionOf(connection, article_id, claim_id):
    try:
        cursor = connection.cursor()

        query = "INSERT INTO CollectionOf (ArticleID, ClaimID) VALUES (%s, %s)"
        values = (article_id, claim_id)

        cursor.execute(query, values)
        connection.commit()

        print("CollectionOf record added successfully!")

    except mysql.connector.Error as err:
        print("Error:", err)

In [13]:
def add_written_by(connection, article_id, author_id, date):
    try:
        cursor = connection.cursor()

        query = "INSERT INTO WrittenBy (ArticleID, AuthorID, date) VALUES (%s, %s, %s)"
        values = (article_id, author_id, date)

        cursor.execute(query, values)
        connection.commit()

        print("WrittenBy record added successfully!")

    except mysql.connector.Error as err:
        print("Error:", err)

In [15]:
def load_database(db, data_file_name, claims_file_name): 
    data_list = pd.read_csv(data_file_name, lineterminator='\n')
    claim_list = pd.read_csv(claims_file_name, lineterminator='\n')
    for index, row in data_list.iterrows():
      articleID = row[0]
      headline = row[1]
      pubname = row[2]
      author = row[3]
      date = row[4]
      url = row[5]
      authorID = str(uuid.uuid4())
      add_article(db,articleID,url)
      add_article_details(db,url,headline,pubname)
      add_author(db,authorID,author)
      add_written_by(db,articleID,authorID,date)
      add_publisher(db,pubname)

      # create a push claims list


    for index, row in claim_list.iterrows():
        articleID = row['id']
        claim = row.get('text',"")
        claimID = row['claimID']
        claim_type = row['claimType']
        numCitations = row['#citations']
        add_claim(db,claimID,claim_type,numCitations,claim)
        add_collectionOf(db,articleID,claimID)


In [29]:
load_database(db,'data_final_50000.csv','claims_final_50000.csv')

Article added successfully!
ArticleDetails added successfully!
Author added successfully!
WrittenBy record added successfully!
Publisher added successfully!
Article added successfully!
ArticleDetails added successfully!
Author added successfully!
WrittenBy record added successfully!
Error: 1062 (23000): Duplicate entry 'NPR' for key 'publisher.PRIMARY'
Article added successfully!
ArticleDetails added successfully!
Author added successfully!
WrittenBy record added successfully!
Error: 1062 (23000): Duplicate entry 'NPR' for key 'publisher.PRIMARY'
Article added successfully!
ArticleDetails added successfully!
Author added successfully!
WrittenBy record added successfully!
Publisher added successfully!
Article added successfully!
ArticleDetails added successfully!
Author added successfully!
WrittenBy record added successfully!
Error: 1062 (23000): Duplicate entry 'Guardian' for key 'publisher.PRIMARY'
Article added successfully!
ArticleDetails added successfully!
Author added successfull